In [1]:
import numpy as np
import matplotlib.pyplot as plt
from pathlib import Path
import librosa
import sklearn
import tensorflow as tf
from tensorflow.keras.callbacks import CSVLogger, EarlyStopping, ModelCheckpoint
import pandas as pd
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix, ConfusionMatrixDisplay
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
plt.style.use("seaborn-v0_8")
import os
import soundfile as sf

Matplotlib is building the font cache; this may take a moment.
2025-05-28 17:31:48.763689: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [2]:
fn_csv = 'scenes_stereo\dcase2013_task1_filenamekey.csv'
df = pd.read_csv(fn_csv)
files = []
labels = []
files = df['decodedname'] #così l'ho chiamato nel file CSV
labels = df['label'] # così l'ho chiamato nel file CSV
print(len(files))
print(len(labels))

audio_path = 'scenes_stereo/scenes_stereo/'


<>:1: SyntaxWarning: invalid escape sequence '\d'
<>:1: SyntaxWarning: invalid escape sequence '\d'
/var/folders/20/3z_k_h2n17q0q6yzv_3_00f40000gn/T/ipykernel_45116/1964878201.py:1: SyntaxWarning: invalid escape sequence '\d'
  fn_csv = 'scenes_stereo\dcase2013_task1_filenamekey.csv'
/var/folders/20/3z_k_h2n17q0q6yzv_3_00f40000gn/T/ipykernel_45116/1964878201.py:1: SyntaxWarning: invalid escape sequence '\d'
  fn_csv = 'scenes_stereo\dcase2013_task1_filenamekey.csv'


FileNotFoundError: [Errno 2] No such file or directory: 'scenes_stereo\\dcase2013_task1_filenamekey.csv'

In [29]:
# Suddividi in train (150) e test (50)
files_train, files_test, labels_train, labels_test = train_test_split(
    files, labels, test_size=50, random_state=42, shuffle=True
)

print(len(files_train))  # 150
print(len(files_test))   # 50
print(len(labels_train))  # 150
print(len(labels_test))   # 50



150
50
150
50


In [24]:
# === CREAZIONE DEI SEGNALI AUGMENTATI (in memoria) ===
import librosa

augmented_data = []

for i, file in enumerate(files_train):
    signal, sr = librosa.load(audio_path + file, sr=16000)
    label = labels_train.iloc[i]
    base_name = os.path.splitext(file)[0]  # es: 'bus12.wav' → 'bus12'

    # Aggiungi il segnale originale
    augmented_data.append((signal, label, f"{base_name}_orig.wav"))

    # Crea versioni augmentate
    versions = {
        'stretch_fast': librosa.effects.time_stretch(signal, rate=1.2),
        'stretch_slow': librosa.effects.time_stretch(signal, rate=0.8),
        'pitch_up': librosa.effects.pitch_shift(signal, sr=sr, n_steps=2),
        'pitch_down': librosa.effects.pitch_shift(signal, sr=sr, n_steps=-2)
    }

    # Aggiungi i segnali augmentati alla lista
    for suffix, aug_signal in versions.items():
        filename = f"{base_name}_{suffix}.wav"
        augmented_data.append((aug_signal, label, filename))


In [25]:
# === SALVATAGGIO DEI FILE AUGMENTATI SU DISCO ===
import os
import soundfile as sf

augmented_path = 'scenes_stereo_augmented/'
os.makedirs(augmented_path, exist_ok=True)

files_train_aug = []
labels_train_aug = []

for signal, label, filename in augmented_data:
    filepath = os.path.join(augmented_path, filename)
    sf.write(filepath, signal, 16000)  # salva a 16kHz

    files_train_aug.append(filename)
    labels_train_aug.append(label)


In [32]:
print(len(files_train_aug))
print(len(files_test))
print(len(labels_train_aug))
print(len(labels_test))

750
50
750
50


In [31]:

# Percorso dei file originali di test
test_path = 'scenes_stereo/scenes_stereo/'  # Adatta se il path è diverso

# Esegui la riproduzione dei primi N file di test (modifica N se vuoi di più)
N = 5  # ad esempio, i primi 5
for i in range(N):
    file = files_test.iloc[i] if isinstance(files_test, pd.Series) else files_test[i]
    file_path = test_path + file

    # Carica e riproduci
    signal, sr = librosa.load(file_path, sr=16000)
    print(f"Playing: {file}")
    display(Audio(data=signal, rate=sr))

#ho verificato che effettivammente fossero quelli di test e quelli di train
    

Playing: busystreet05.wav


Playing: restaurant06.wav


Playing: park07.wav


Playing: office18.wav


Playing: bus12.wav
